In [6]:
import requests
import json
import pandas as pd
from pandas import json_normalize
import config
from db_manager import DBManager
import os
from rest_api import Api
from datetime import date
from dateutil.relativedelta import relativedelta
from urllib.parse import quote_plus
from sqlalchemy import create_engine
import itertools
import logging

In [7]:
logging.basicConfig(
    format='%(levelname)s-%(lineno)s-%(message)s',
    datefmt='%Y-%m-%d %H:%M:%S',
    level='INFO'
)
logger=logging.getLogger(__name__)

#### Show all columns without truncating

Today's date

In [8]:
today = date.today()
print(today)

2023-08-23


Adding months to today's date. Near term travel dates 30 - 60 days ahead

In [9]:
departure_date_1_month = today + relativedelta(months=1)
departure_date_2_month = today + relativedelta(months=2)
return_date_1_month = departure_date_2_month
return_date_2_month = today + relativedelta(months=3)
logger.info(f'Departure_dates:{departure_date_1_month} and {departure_date_2_month} \nReturn dates:{return_date_1_month} and {return_date_2_month}')

INFO-__main__:5-Departure_dates:2023-09-23 and 2023-10-23 
Return dates:2023-10-23 and 2023-11-23


Get the nearby festival departure dates by start_date from the public.indian_holidays table

In [11]:
# credentials=config.pg_credentials
# db = DBManager(credentials=credentials)
# df_departure_arrival_dates = db.run_query(query_file_name='festival_dates')

In [12]:
#df_departure_arrival_dates 

Apply the combination of params to get data for all possible combinations of depart, arrival dates and depart arrival airports

Combination itertools usage. Im calculating the total combinations by multiplying the number of possibilities (unique values) for each variable<br />
Departure airport: 2 possibilities<br />
Arrival airport: 4 possibilities<br />
Departure date: 2 possibilities<br />
Arrival date: 1 possibilities<br />
Total combinations = 2 x 4 x 2 x 1 = 16 combinations

#### Travel payouts API to get flight search results for each combination in the list 

--------------------------------------------------------

API test for amadeus

POST request to the Amadeus authorization server to get the access token

In [14]:
response = requests.post(url=config.url_token, headers=config.headers_token, data=config.data)

if response.status_code == 200:
  # API call succeeded
  token = response.json()['access_token'] 
  logger.info('Successful access token generation')
else:
  # API call failed
  print(response.text)

INFO-__main__:6-Successful access token generation


In [15]:
#Combinations of destination and origin airport codes
origins = config.params['originLocationCode']
destinations = config.params['destinationLocationCode']
departure_dates=[departure_date_1_month,departure_date_2_month]
# return_dates=[return_date_1_month,return_date_2_month]

Creating combinations of Origin and Destination to be passed as parameters to the api call

trial

In [16]:
headers = {
  'client_id': config.client_id, 
  'client_secret': config.client_secret,
  'Authorization': f'Bearer {token}'
  }

url = config.url

response = []
counter = 0

for origin, dest, depart in itertools.product(origins, destinations, departure_dates):

    params={
        'originLocationCode': origin,
        'destinationLocationCode':dest, 
        'departureDate': depart, 
        'returnDate' : None,
        'adults':1,
        'children':None,
        'infants':None,
        'travelClass':None,
        'currencyCode':'EUR',
        'maxPrice' : None
        }


    #to be worked on later for by calling rest_api module
    # api = Api()
    # resp = api.make_flight_api_request(url,headers,params)
    resp = requests.get(url, headers=headers, params=params)
    counter = counter+1
    resp = resp.json()
    response.append(resp)
    logger.info(f'API call {counter} succeeded for flight offers')
    # else:
    #     # API call failed
    #     logger.info('API call failed')


INFO-__main__:35-API call 1 succeeded for flight offers
INFO-__main__:35-API call 2 succeeded for flight offers
INFO-__main__:35-API call 3 succeeded for flight offers
INFO-__main__:35-API call 4 succeeded for flight offers
INFO-__main__:35-API call 5 succeeded for flight offers
INFO-__main__:35-API call 6 succeeded for flight offers
INFO-__main__:35-API call 7 succeeded for flight offers
INFO-__main__:35-API call 8 succeeded for flight offers
INFO-__main__:35-API call 9 succeeded for flight offers
INFO-__main__:35-API call 10 succeeded for flight offers
INFO-__main__:35-API call 11 succeeded for flight offers
INFO-__main__:35-API call 12 succeeded for flight offers
INFO-__main__:35-API call 13 succeeded for flight offers
INFO-__main__:35-API call 14 succeeded for flight offers
INFO-__main__:35-API call 15 succeeded for flight offers
INFO-__main__:35-API call 16 succeeded for flight offers


In [126]:
response

[{'meta': {'count': 121,
   'links': {'self': 'https://test.api.amadeus.com/v2/shopping/flight-offers?originLocationCode=BER&destinationLocationCode=DEL&departureDate=2023-09-23&adults=1&currencyCode=EUR'}},
  'data': [{'type': 'flight-offer',
    'id': '1',
    'source': 'GDS',
    'instantTicketingRequired': False,
    'nonHomogeneous': False,
    'oneWay': False,
    'lastTicketingDate': '2023-08-24',
    'lastTicketingDateTime': '2023-08-24',
    'numberOfBookableSeats': 2,
    'itineraries': [{'duration': 'PT11H40M',
      'segments': [{'departure': {'iataCode': 'BER',
         'at': '2023-09-23T10:45:00'},
        'arrival': {'iataCode': 'AMS', 'at': '2023-09-23T12:10:00'},
        'carrierCode': 'KL',
        'number': '1820',
        'aircraft': {'code': 'E90'},
        'duration': 'PT1H25M',
        'id': '202',
        'numberOfStops': 0,
        'blacklistedInEU': False},
       {'departure': {'iataCode': 'AMS', 'at': '2023-09-23T14:10:00'},
        'arrival': {'iataCode': '

Convert that sample nested JSON data into separate DataFrames

In [107]:
# Flight offers DataFrame
for r in response: 
    offers_df = pd.DataFrame(r['data'])
    # Itineraries DataFrame
    itineraries_df = pd.json_normalize(r['data'], record_path='itineraries', meta=['id', 'source'])
    # # Traveler pricing DataFrame
    traveler_pricing_df = pd.json_normalize(r['data'], record_path=['travelerPricings'], meta=['id', 'source'])


Treating the itineraries df

In [87]:
# Explode the 'segment' column to create separate rows for each dictionary
exploded_df = itineraries_df.explode('segments')

# Apply json_normalize to the 'segment' column to split dictionaries into separate columns
normalized_df = json_normalize(exploded_df['segments']).add_suffix('_segments')

# Join the exploded and normalized DataFrames
final_df = exploded_df.drop('segments', axis=1).join(normalized_df)

# Drop duplicates based on all columns to deduplicate the DataFrame
deduplicated_df = final_df.drop_duplicates()

# If you want to reset the index of the deduplicated DataFrame
deduplicated_df.reset_index(drop=True, inplace=True)
deduplicated_df=deduplicated_df.drop(columns=['id_segments'])

# Remove the added '_segment' suffix from column names
deduplicated_df.columns = deduplicated_df.columns.str.replace('_segments$', '', regex=True)

#replace . in column anmes by underscore
deduplicated_df.columns = deduplicated_df.columns.str.replace('.', '_', regex=False)

#Assigning to itineraries df
itineraries_df = deduplicated_df

#drop unwanted columns 
itineraries_df=itineraries_df.drop(columns=['blacklistedInEU','departure_terminal','arrival_terminal'])


Treating traveler_pricing_df

In [108]:
# Explode the 'segment' column to create separate rows for each dictionary
exploded_df = traveler_pricing_df.explode('fareDetailsBySegment')

# Apply json_normalize to the 'segment' column to split dictionaries into separate columns
normalized_df = json_normalize(exploded_df['fareDetailsBySegment']).add_suffix('_fare')

# Join the exploded and normalized DataFrames
final_df = exploded_df.drop('fareDetailsBySegment', axis=1).join(normalized_df)

# Drop duplicates based on all columns to deduplicate the DataFrame
deduplicated_df = final_df.drop_duplicates()

# # If you want to reset the index of the deduplicated DataFrame
deduplicated_df.reset_index(drop=True, inplace=True)
# deduplicated_df=deduplicated_df.drop(columns=['id_segments'])

# # Remove the added '_segment' suffix from column names
deduplicated_df.columns = deduplicated_df.columns.str.replace('_fare$', '', regex=True)

# #replace . in column anmes by underscore
deduplicated_df.columns = deduplicated_df.columns.str.replace('.', '_', regex=False)

# #Assigning to itineraries df
traveler_pricing_df = deduplicated_df

# #drop unwanted columns 
traveler_pricing_df=traveler_pricing_df.drop(columns=['fareBasis','class','brandedFare'])


Treating price in offers_df

In [116]:
# Explode the 'segment' column to create separate rows for each dictionary
exploded_df = offers_df.explode('price')

# # Apply json_normalize to the 'segment' column to split dictionaries into separate columns
# normalized_df = json_normalize(exploded_df['fareDetailsBySegment']).add_suffix('_fare')

# # Join the exploded and normalized DataFrames
# final_df = exploded_df.drop('fareDetailsBySegment', axis=1).join(normalized_df)

# # Drop duplicates based on all columns to deduplicate the DataFrame
# deduplicated_df = final_df.drop_duplicates()

# # # If you want to reset the index of the deduplicated DataFrame
# deduplicated_df.reset_index(drop=True, inplace=True)
# # deduplicated_df=deduplicated_df.drop(columns=['id_segments'])

# # # Remove the added '_segment' suffix from column names
# deduplicated_df.columns = deduplicated_df.columns.str.replace('_fare$', '', regex=True)

# # #replace . in column anmes by underscore
# deduplicated_df.columns = deduplicated_df.columns.str.replace('.', '_', regex=False)

# # #Assigning to itineraries df
# traveler_pricing_df = deduplicated_df

# # #drop unwanted columns 
# traveler_pricing_df=traveler_pricing_df.drop(columns=['fareBasis','class','brandedFare'])

In [117]:
exploded_df.head()

type id source  instantTicketingRequired  nonHomogeneous  oneWay  \
0  flight-offer  1    GDS                     False           False   False   
0  flight-offer  1    GDS                     False           False   False   
0  flight-offer  1    GDS                     False           False   False   
0  flight-offer  1    GDS                     False           False   False   
0  flight-offer  1    GDS                     False           False   False   

  lastTicketingDate lastTicketingDateTime  numberOfBookableSeats  \
0        2023-10-23            2023-10-23                      1   
0        2023-10-23            2023-10-23                      1   
0        2023-10-23            2023-10-23                      1   
0        2023-10-23            2023-10-23                      1   
0        2023-10-23            2023-10-23                      1   

                                         itineraries       price  \
0  [{'duration': 'PT18H30M', 'segments': [{'depar...    currency   
0  [{'duration': 'PT18H30M', 'segments': [{'depar...       total   
0  [{'duration': 'PT18H30M', 'segments': [{'depar...        base   
0  [{'duration': 'PT18H30M', 'segments': [{'depar...        fees   
0  [{'duration': 'PT18H30M', 'segments': [{'depar...  grandTotal   

                                      pricingOptions validatingAirlineCodes  \
0  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [AI]   
0  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [AI]   
0  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [AI]   
0  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [AI]   
0  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [AI]   

                                    travelerPricings  
0  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
0  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
0  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
0  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
0  [{'travelerId': '1', 'fareOption': 'STANDARD',...

Dropping unwanted columns from the above respective tables

In [86]:
# prices_df=prices_df.drop(columns=['fees','additionalServices'])
# offers_df=offers_df.drop(columns=['itineraries','price','pricingOptions','travelerPricings'])
offers_df

To split a column containing a list of dictionaries into multiple columns in a DataFrame, avoiding duplication, you can:

Explode the list column to rows
Pivot the exploded rows into columns

---------------------------------------------------

Dropping unwanted columns

In [62]:
new_df_legs=new_df_legs.drop(columns=['departureTimeMinutes','arrivalTimeMinutes','segments','operatingAirlineCodes','stopoverCode','shortStopover','earlyDeparture','lateArrival','newAircraft','oldAircraft','highlyRatedCarrier','score'])

In [89]:
new_df_legs['incremental_day']=today

In [115]:
credentials=config.pg_credentials
db = DBManager(credentials=credentials)
db.create_table_from_df(df=new_df_fares,table_name='fares')

INFO-db_manager:30-Keerthana%40123
INFO-db_manager:32-CONNECTED
INFO-db_manager:67-Dumped to DB
